## Rede Neural Convolucional ( CNN ) -  Introdução __________________________________

## Exemplo com base de dados rotulada de imagens (MNIST)

Importar as bibliotecas

In [7]:
import tensorflow as tf
from tensorflow import keras
import numpy as np

## Dividir a base de dados em conjuntos de treinamento e teste e normalizar.

 - 1 - Carregar a base de dados Fashion MNIST e divida-a em conjuntos de treinamento e teste.
 - 2 - Pré-processamento dos dados:
 - 3 - Normalizar os pixels da imagem para que estejam entre 0 e 1.
 - 4 Transforar os rótulos em vetores de categoria.

In [2]:
# Download da base de dados Fashion MNIST
(x_train, y_train), (x_test, y_test) = keras.datasets.fashion_mnist.load_data()

# Normalizando as imagens
x_train = x_train / 255.0
x_test = x_test / 255.0

y_train = keras.utils.to_categorical(y_train, num_classes=10)
y_test = keras.utils.to_categorical(y_test, num_classes=10)

4422102/4422102 [==============================] - 0s 0us/step


## Arquitetura da Rede Neural Convolucional

In [3]:
# Definindo a arquitetura da CNN
model = keras.Sequential()
model.add(keras.layers.Conv2D(32, (3,3), activation='relu', input_shape=(28, 28, 1)))
model.add(keras.layers.MaxPooling2D((2,2)))
model.add(keras.layers.Conv2D(64, (3,3), activation='relu'))
model.add(keras.layers.MaxPooling2D((2,2)))
model.add(keras.layers.Conv2D(64, (3,3), activation='relu')) ##
model.add(keras.layers.MaxPooling2D((2, 2))) ##
model.add(keras.layers.Flatten())
model.add(keras.layers.Dense(128, activation='relu'))
model.add(keras.layers.Dense(10, activation='softmax'))
model.summary()


# Compilando o modelo
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])


# Treinando o modelo
model.fit(x_train, y_train, epochs=50)

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 26, 26, 32)        320       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 13, 13, 32)       0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 11, 11, 64)        18496     
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 5, 5, 64)         0         
 2D)                                                             
                                                                 
 conv2d_2 (Conv2D)           (None, 3, 3, 64)          36928     
                                                                 
 max_pooling2d_2 (MaxPooling  (None, 1, 1, 64)         0

## Avaliação do modelo 

Uma métrica comum para avaliar o desempenho de um modelo de classificação é a acurácia, que mede a porcentagem de previsões corretas do modelo. Pode-se calcular a acurácia do seu modelo no conjunto de teste da seguinte maneira:

In [4]:
# Avaliando o modelo no conjunto de teste
test_loss, test_acc = model.evaluate(x_test, y_test)
print('Acuracia do teste:', test_acc)

313/313 [==============================] - 2s 7ms/step - loss: 0.8573 - accuracy: 0.8876
Acuracia do teste: 0.8876000046730042


A acurácia é uma métrica comum para avaliar o desempenho de um modelo de classificação e é definida como a porcentagem de previsões corretas do modelo. Portanto, uma acurácia de 89% significa que o modelo conseguiu prever corretamente 89% das classes das imagens do conjunto de teste.

É importante lembrar que a acurácia por si só pode não ser uma medida suficientemente boa do desempenho do modelo, pois ela não leva em consideração o desbalanceamento de classes. Por exemplo, se o conjunto de dados tiver 90% de imagens de uma classe e 10% de imagens de outra classe, um modelo que sempre preveja a classe mais prevalente terá uma acurácia de 90%, mas isso não significa que o modelo esteja realmente aprendendo a distinguir as duas classes. Nesses casos, é importante avaliar o modelo usando outras métricas, como a matriz de confusão abaixo, que mostra que na diagonal principal os volumes de acertos realmente apontam para um bom desempenho do modelo.

In [8]:
from sklearn.metrics import confusion_matrix
y_pred = model.predict(x_test)
y_pred = np.argmax(y_pred, axis=1)

y_test = np.argmax(y_test, axis=-1)

print('Matriz de Confusao')

confusion_matrix(y_test, y_pred)

313/313 [==============================] - 2s 7ms/step
Matriz de Confusao


array([[861,   0,  24,  19,   7,   2,  79,   0,   8,   0],
       [  3, 974,   4,  13,   4,   0,   2,   0,   0,   0],
       [ 19,   0, 820,  17,  82,   0,  62,   0,   0,   0],
       [ 31,  12,  18, 875,  37,   0,  27,   0,   0,   0],
       [  2,   1,  43,  23, 876,   0,  54,   0,   1,   0],
       [  2,   0,   0,   0,   0, 976,   0,  14,   1,   7],
       [136,   1,  72,  33, 127,   0, 625,   0,   6,   0],
       [  0,   0,   0,   0,   0,  10,   0, 974,   0,  16],
       [  7,   0,   5,   3,  11,   5,   9,   1, 958,   1],
       [  1,   0,   0,   0,   1,  10,   0,  51,   0, 937]], dtype=int64)

### Redução da dimensionalidade por Encoder + MLP

Um encoder é uma parte de uma rede neural que é usada para codificar os dados de entrada em uma representação de menor dimensionalidade, geralmente com o objetivo de reduzir a complexidade dos dados ou para facilitar a generalização do modelo.


1 - Definir a arquitetura do encoder. Isso inclui escolher o número de camadas, o número de filtros em cada camada, o tamanho dos filtros e a função de ativação a ser usada. 

2 - Compilar o encoder. Escolher uma função de perda, um otimizador e uma métrica para avaliar o desempenho do encoder.

3 - Treinar o encoder. Fornecer os conjuntos de treinamento e validação ao encoder e especificar o número de épocas e o tamanho do lote. 

4 - Usar o encoder para codificar as imagens de entrada. Isso pode ser feito usando o método predict do encoder e passando as imagens como entrada, resultando em uma representação codificada de menor dimensionalidade das imagens.

In [9]:
# Refazer para nao travar a memoria da GPU
import tensorflow as tf
from tensorflow import keras

(x_train, y_train), (x_test, y_test) = keras.datasets.fashion_mnist.load_data()

x_train = x_train / 255.0
x_test = x_test / 255.0

y_train = keras.utils.to_categorical(y_train, num_classes=10)
y_test = keras.utils.to_categorical(y_test, num_classes=10)

x_train = x_train.reshape(-1, 28, 28, 1)
x_test = x_test.reshape(-1, 28, 28, 1)


# Arquitetura do Encoder
encoder_input = keras.Input(shape=(28, 28, 1))
x = keras.layers.Conv2D(32, (3, 3), activation='relu')(encoder_input)
x = keras.layers.MaxPooling2D((2, 2))(x)
x = keras.layers.Conv2D(64, (3, 3), activation='relu')(x)
x = keras.layers.MaxPooling2D((2, 2))(x)
encoder_output = keras.layers.Flatten()(x)

encoder = keras.Model(encoder_input, encoder_output)

# Arquitetura do MLP
mlp_input = keras.Input(shape=(encoder.output_shape[1],))
x = keras.layers.Dense(64, activation='relu')(mlp_input)
x = keras.layers.Dense(32, activation='relu')(x)
mlp_output = keras.layers.Dense(10, activation='softmax')(x)

mlp = keras.Model(mlp_input, mlp_output)

# Juntando o Encoder e o MLP
model = keras.Model(encoder_input, mlp(encoder_output))

# Compilando
model.compile(optimizer='adam',
              loss='categorical_crossentropy',
              metrics=['accuracy'])

# Treinando
model.fit(x_train, y_train, epochs=50)


Epoch 1/50
1875/1875 [==============================] - 31s 16ms/step - loss: 0.4976 - accuracy: 0.8187
Epoch 2/50
1875/1875 [==============================] - 30s 16ms/step - loss: 0.3258 - accuracy: 0.8818
Epoch 3/50
1875/1875 [==============================] - 29s 15ms/step - loss: 0.2759 - accuracy: 0.8999
Epoch 4/50
1875/1875 [==============================] - 29s 16ms/step - loss: 0.2427 - accuracy: 0.9099
Epoch 5/50
1875/1875 [==============================] - 29s 16ms/step - loss: 0.2186 - accuracy: 0.9191
Epoch 6/50
1875/1875 [==============================] - 30s 16ms/step - loss: 0.1970 - accuracy: 0.9263
Epoch 7/50
1875/1875 [==============================] - 29s 16ms/step - loss: 0.1774 - accuracy: 0.9346
Epoch 8/50
1875/1875 [==============================] - 30s 16ms/step - loss: 0.1604 - accuracy: 0.9411
Epoch 9/50
1875/1875 [==============================] - 30s 16ms/step - loss: 0.1481 - accuracy: 0.9443
Epoch 10/50
1875/1875 [==============================] - 29s 16m

## Comparativo

In [30]:
test_loss, test_acc = model.evaluate(x_test, y_test)
print('Acuracia do teste:', test_acc)

313/313 [==============================] - 1s 3ms/step - loss: 0.7093 - accuracy: 0.9077
Acuracia do teste: 0.9077000021934509


A acuracia de 90%, praticamente igual ao resultado observado na rede neural convolucional.
Comparando a matriz de confusao das duas tecnicas, pode-se observar que ambas apresentaram valores baixos apenas para a setima coluna, sendo:
63% para a CNN
74% para o MLP + Encoder


In [31]:
from sklearn.metrics import confusion_matrix
y_pred = model.predict(x_test)
y_pred = np.argmax(y_pred, axis=1)

y_test = np.argmax(y_test, axis=-1)

print('Matriz de Confusao')

confusion_matrix(y_test, y_pred)

313/313 [==============================] - 1s 2ms/step
Matriz de Confusao


array([[843,   1,  25,  10,   7,   1, 110,   0,   3,   0],
       [  0, 984,   2,   7,   3,   0,   2,   0,   2,   0],
       [ 19,   0, 850,  10,  64,   2,  55,   0,   0,   0],
       [ 21,   8,   7, 891,  36,   2,  33,   0,   2,   0],
       [  2,   0,  35,  21, 886,   0,  54,   0,   1,   1],
       [  0,   0,   0,   0,   0, 981,   0,  13,   0,   6],
       [ 88,   1,  67,  27,  64,   1, 745,   0,   7,   0],
       [  0,   1,   0,   0,   0,  14,   0, 959,   0,  26],
       [  6,   0,   5,   3,   4,   2,   2,   2, 975,   1],
       [  0,   0,   1,   0,   0,   6,   0,  30,   0, 963]])